**Author:** Mattias Östmar, mattiasostmar@gmail.com

**Published:** 2019-03-36

# Create pickled Pandas Dataframe with texts without paragraph separation

In this notebook we follow the text extraction method suggested in the [Term frequency extractor script](https://pan.webis.de/semeval19/semeval19-code/semeval-pan-2019-tf-extractor.py) on the [Hyperpartisan News Detetction PAN @SemEval 2019](https://pan.webis.de/semeval19/semeval19-web/) web page. 

When comparing the results from discoursebias software, the results we're exactly the same.

In [1]:
import sys
sys.path.append('../discoursebias/') # replace with your path to discoursebias library
import discoursebias as dib

import os
import getopt
import xml.sax
import lxml.sax
import lxml.etree
import re
import json
import pandas as pd

The point of this notebook, very similar to `create_unparagraphed_texts_in_pandas_dataframe_from_xml_bypublisher.ipynb`, is to compare the biasIndex when `<p>` are not taking into account, that is the equivalent to `\n\n` in the notebook "process_pandas_dataframe_texts_with_discoursebias". This might affect the calculation of the biasIndex severly. This code is the [Term Frequency Exctractor code](https://pan.webis.de/semeval19/semeval19-code/semeval-pan-2019-tf-extractor.py) published at [https://pan.webis.de/semeval19/semeval19-web/index.html](https://pan.webis.de/semeval19/semeval19-web/index.html) to illustrate how to read the texts in the hyperpartisan news dataset.

In [2]:
########## SAX FOR STREAM PARSING ##########
class HyperpartisanNewsTFExtractor(xml.sax.ContentHandler):
    def __init__(self, outFile):
        xml.sax.ContentHandler.__init__(self)
        self.outFile = outFile
        self.lxmlhandler = "undefined"

    def startElement(self, name, attrs):
        if name != "articles":
            if name == "article":
                self.lxmlhandler = lxml.sax.ElementTreeContentHandler()

            self.lxmlhandler.startElement(name, attrs)

    def characters(self, data):
        if self.lxmlhandler != "undefined":
            self.lxmlhandler.characters(data)

    def endElement(self, name):
        if self.lxmlhandler != "undefined":
            self.lxmlhandler.endElement(name)
            if name == "article":
                # pass to handleArticle function
                handleArticle(self.lxmlhandler.etree.getroot(), self.outFile)
                self.lxmlhandler = "undefined"

In [9]:
########## ARTICLE HANDLING ##########
def handleArticle(article, outFile):
    obj = {}

    # get text from article
    text = lxml.etree.tostring(article, method="text", encoding="unicode")
    textcleaned = re.sub('[^a-z ]', '', text.lower())
    title = article.get("title")
    
    obj["text"] = title + "\n\n" + textcleaned
    obj["id"] = article.get("id")

    # get discourse bias result
    exp = dib.TextNetwork(textcleaned, textname=obj["id"], plot=False, save_gexf=False)
    result = exp.run()
    obj["biasIndex"] = result.loc["biasIndex"].values[0]
    
    outFile.write(json.dumps(obj))
    outFile.write("\n")

In [10]:
outputFile = "unparagraphed_validation_texts_analyzed_with_discoursebias.jsonl"
with open(outputFile, 'w', buffering=1) as outFile:
    with open("data/articles-validation-bypublisher-20181122.xml", 'r') as inputRunFile:
        parser = xml.sax.make_parser()
        parser.setContentHandler(HyperpartisanNewsTFExtractor(outFile))
        source = xml.sax.xmlreader.InputSource()
        source.setByteStream(inputRunFile)
        source.setEncoding("utf-8")
        parser.parse(source)

0000017 bias index: DIVERSIFIED
0000023 bias index: DIVERSIFIED
0000029 bias index: DIVERSIFIED
0000032 bias index: DIVERSIFIED
0000037 bias index: FOCUSED
0000070 bias index: DIVERSIFIED
0000077 bias index: DIVERSIFIED
0000079 bias index: DIVERSIFIED
0000092 bias index: DIVERSIFIED
0000101 bias index: DIVERSIFIED
0000144 bias index: FOCUSED
0000175 bias index: DIVERSIFIED
0000177 bias index: DIVERSIFIED
0000195 bias index: DIVERSIFIED
0000202 bias index: DIVERSIFIED
0000217 bias index: DIVERSIFIED
0000226 bias index: DIVERSIFIED
0000232 bias index: DIVERSIFIED
0000233 bias index: DIVERSIFIED
0000242 bias index: DIVERSIFIED
0000250 bias index: BIASED
0000254 bias index: DIVERSIFIED
0000255 bias index: DIVERSIFIED
0000280 bias index: DIVERSIFIED
0000281 bias index: FOCUSED
0000282 bias index: DIVERSIFIED
0000283 bias index: FOCUSED
0000292 bias index: DIVERSIFIED
0000301 bias index: FOCUSED
0000305 bias index: DIVERSIFIED
0000307 bias index: DIVERSIFIED
0000311 bias index: DIVERSIFIED
0

0002405 bias index: DIVERSIFIED
0002432 bias index: DISPERSED
0002453 bias index: FOCUSED
0002458 bias index: DISPERSED
0002474 bias index: DIVERSIFIED
0002491 bias index: DIVERSIFIED
0002503 bias index: DIVERSIFIED
0002516 bias index: DIVERSIFIED
0002578 bias index: DIVERSIFIED
0002582 bias index: DIVERSIFIED
0002591 bias index: DIVERSIFIED
0002596 bias index: DIVERSIFIED
0002598 bias index: FOCUSED
0002603 bias index: DIVERSIFIED
0002612 bias index: DIVERSIFIED
0002648 bias index: DIVERSIFIED
0002665 bias index: DIVERSIFIED
0002669 bias index: DIVERSIFIED
0002687 bias index: DIVERSIFIED
0002694 bias index: DIVERSIFIED
0002696 bias index: DIVERSIFIED
0002701 bias index: DIVERSIFIED
0002703 bias index: DIVERSIFIED
0002716 bias index: DIVERSIFIED
0002724 bias index: DIVERSIFIED
0002733 bias index: DIVERSIFIED
0002749 bias index: FOCUSED
0002779 bias index: DIVERSIFIED
0002780 bias index: DISPERSED
0002796 bias index: DIVERSIFIED
0002822 bias index: DIVERSIFIED
0002827 bias index: DIVERS

0005072 bias index: DIVERSIFIED
0005149 bias index: DIVERSIFIED
0005155 bias index: DIVERSIFIED
0005187 bias index: FOCUSED
0005203 bias index: FOCUSED
0005211 bias index: DIVERSIFIED
0005215 bias index: DIVERSIFIED
0005221 bias index: DIVERSIFIED
0005233 bias index: FOCUSED
0005241 bias index: DIVERSIFIED
0005259 bias index: DIVERSIFIED
0005269 bias index: DIVERSIFIED
0005299 bias index: DISPERSED
0005318 bias index: DIVERSIFIED
0005322 bias index: DIVERSIFIED
0005324 bias index: DIVERSIFIED
0005329 bias index: FOCUSED
0005361 bias index: DIVERSIFIED
0005380 bias index: DIVERSIFIED
0005383 bias index: DIVERSIFIED
0005384 bias index: DIVERSIFIED
0005391 bias index: DIVERSIFIED
0005393 bias index: DIVERSIFIED
0005418 bias index: DIVERSIFIED
0005432 bias index: DIVERSIFIED
0005445 bias index: DIVERSIFIED
0005448 bias index: DIVERSIFIED
0005477 bias index: DIVERSIFIED
0005481 bias index: FOCUSED
0005494 bias index: DIVERSIFIED
0005500 bias index: DIVERSIFIED
0005525 bias index: DIVERSIFIE

0007941 bias index: DIVERSIFIED
0007946 bias index: DIVERSIFIED
0007972 bias index: DIVERSIFIED
0007975 bias index: DIVERSIFIED
0007978 bias index: DIVERSIFIED
0007987 bias index: DIVERSIFIED
0007990 bias index: FOCUSED
0008008 bias index: DIVERSIFIED
0008010 bias index: FOCUSED
0008025 bias index: DIVERSIFIED
0008029 bias index: DIVERSIFIED
0008034 bias index: DIVERSIFIED
0008044 bias index: DIVERSIFIED
0008058 bias index: DIVERSIFIED
0008059 bias index: DISPERSED
0008069 bias index: DIVERSIFIED
0008094 bias index: DIVERSIFIED
0008103 bias index: DIVERSIFIED
0008134 bias index: FOCUSED
0008146 bias index: DIVERSIFIED
0008163 bias index: DIVERSIFIED
0008184 bias index: DIVERSIFIED
0008190 bias index: DIVERSIFIED
0008192 bias index: DIVERSIFIED
0008205 bias index: DIVERSIFIED
0008215 bias index: FOCUSED
0008222 bias index: DIVERSIFIED
0008239 bias index: DIVERSIFIED
0008244 bias index: DIVERSIFIED
0008247 bias index: DIVERSIFIED
0008261 bias index: FOCUSED
0008275 bias index: FOCUSED
00

0010358 bias index: DIVERSIFIED
0010363 bias index: DIVERSIFIED
0010393 bias index: DIVERSIFIED
0010398 bias index: FOCUSED
0010415 bias index: DIVERSIFIED
0010419 bias index: DIVERSIFIED
0010431 bias index: FOCUSED
0010433 bias index: DIVERSIFIED
0010436 bias index: DIVERSIFIED
0010440 bias index: DIVERSIFIED
0010446 bias index: DIVERSIFIED
0010449 bias index: DIVERSIFIED
0010458 bias index: DIVERSIFIED
0010461 bias index: DIVERSIFIED
0010465 bias index: DIVERSIFIED
0010480 bias index: DIVERSIFIED
0010500 bias index: DIVERSIFIED
0010513 bias index: DIVERSIFIED
0010524 bias index: DIVERSIFIED
0010561 bias index: DIVERSIFIED
0010603 bias index: DIVERSIFIED
0010606 bias index: DIVERSIFIED
0010613 bias index: DIVERSIFIED
0010619 bias index: DIVERSIFIED
0010628 bias index: DIVERSIFIED
0010635 bias index: DIVERSIFIED
0010669 bias index: DIVERSIFIED
0010681 bias index: DIVERSIFIED
0010710 bias index: DIVERSIFIED
0010715 bias index: DIVERSIFIED
0010719 bias index: DIVERSIFIED
0010721 bias ind

...

1484233 bias index: DIVERSIFIED
1484244 bias index: DIVERSIFIED
1484247 bias index: DIVERSIFIED
1484260 bias index: DIVERSIFIED
1484264 bias index: DIVERSIFIED
1484266 bias index: DIVERSIFIED
1484269 bias index: DIVERSIFIED
1484300 bias index: DIVERSIFIED
1484308 bias index: DIVERSIFIED
1484325 bias index: DIVERSIFIED
1484332 bias index: DIVERSIFIED
1484354 bias index: DIVERSIFIED
1484358 bias index: FOCUSED
1484379 bias index: DIVERSIFIED
1484393 bias index: DIVERSIFIED
1484404 bias index: DIVERSIFIED
1484425 bias index: DIVERSIFIED
1484437 bias index: DIVERSIFIED
1484450 bias index: DIVERSIFIED
1484482 bias index: DIVERSIFIED
1484486 bias index: DIVERSIFIED
1484518 bias index: DIVERSIFIED
1484524 bias index: DIVERSIFIED
1484525 bias index: DIVERSIFIED
1484528 bias index: DIVERSIFIED
1484538 bias index: DIVERSIFIED
1484544 bias index: DIVERSIFIED
1484554 bias index: DIVERSIFIED
1484560 bias index: DIVERSIFIED
1484574 bias index: DIVERSIFIED
1484575 bias index: DIVERSIFIED
1484580 bias

1486857 bias index: DIVERSIFIED
1486881 bias index: DIVERSIFIED
1486887 bias index: DIVERSIFIED
1486891 bias index: DIVERSIFIED
1486896 bias index: DISPERSED
1486904 bias index: DIVERSIFIED
1486907 bias index: FOCUSED
1486910 bias index: DIVERSIFIED
1486915 bias index: FOCUSED
1486919 bias index: DIVERSIFIED
1486930 bias index: DIVERSIFIED
1486938 bias index: DIVERSIFIED
1486957 bias index: DIVERSIFIED
1486958 bias index: FOCUSED
1486971 bias index: DIVERSIFIED
1486975 bias index: FOCUSED
1486979 bias index: FOCUSED
1486988 bias index: DIVERSIFIED
1486991 bias index: DIVERSIFIED
1486992 bias index: DIVERSIFIED
1487000 bias index: DIVERSIFIED
1487021 bias index: DIVERSIFIED
1487026 bias index: DIVERSIFIED
1487028 bias index: DIVERSIFIED
1487092 bias index: DIVERSIFIED
1487102 bias index: DIVERSIFIED
1487111 bias index: DIVERSIFIED
1487119 bias index: DIVERSIFIED
1487125 bias index: DIVERSIFIED
1487140 bias index: FOCUSED
1487143 bias index: BIASED
1487174 bias index: DIVERSIFIED
1487178

1489403 bias index: DIVERSIFIED
1489420 bias index: DIVERSIFIED
1489424 bias index: FOCUSED
1489450 bias index: DIVERSIFIED
1489453 bias index: DIVERSIFIED
1489475 bias index: FOCUSED
1489507 bias index: DIVERSIFIED
1489517 bias index: DIVERSIFIED
1489520 bias index: DISPERSED
1489530 bias index: DIVERSIFIED
1489533 bias index: DIVERSIFIED
1489544 bias index: DIVERSIFIED
1489547 bias index: DIVERSIFIED
1489552 bias index: DIVERSIFIED
1489565 bias index: DIVERSIFIED
1489578 bias index: DIVERSIFIED
1489584 bias index: DIVERSIFIED
1489596 bias index: DIVERSIFIED
1489632 bias index: DIVERSIFIED
1489637 bias index: DIVERSIFIED
1489638 bias index: DIVERSIFIED
1489641 bias index: DIVERSIFIED
1489653 bias index: DIVERSIFIED
1489662 bias index: DIVERSIFIED
1489693 bias index: DIVERSIFIED
1489694 bias index: DISPERSED
1489695 bias index: DIVERSIFIED
1489723 bias index: DIVERSIFIED
1489734 bias index: DIVERSIFIED
1489744 bias index: DIVERSIFIED
1489777 bias index: FOCUSED
1489787 bias index: DIVE

1492098 bias index: DIVERSIFIED
1492127 bias index: DIVERSIFIED
1492133 bias index: DIVERSIFIED
1492167 bias index: DISPERSED
1492169 bias index: DIVERSIFIED
1492171 bias index: DIVERSIFIED
1492193 bias index: DIVERSIFIED
1492201 bias index: DIVERSIFIED
1492216 bias index: DIVERSIFIED
1492243 bias index: DIVERSIFIED
1492253 bias index: DIVERSIFIED
1492255 bias index: DIVERSIFIED
1492259 bias index: DIVERSIFIED
1492269 bias index: DIVERSIFIED
1492276 bias index: FOCUSED
1492286 bias index: DIVERSIFIED
1492308 bias index: DIVERSIFIED
1492311 bias index: DIVERSIFIED
1492327 bias index: DIVERSIFIED
1492328 bias index: FOCUSED
1492381 bias index: DIVERSIFIED
1492382 bias index: FOCUSED
1492385 bias index: DIVERSIFIED
1492386 bias index: DIVERSIFIED
1492400 bias index: DIVERSIFIED
1492404 bias index: DIVERSIFIED
1492408 bias index: DIVERSIFIED
1492421 bias index: DIVERSIFIED
1492426 bias index: DIVERSIFIED
1492470 bias index: DIVERSIFIED
1492481 bias index: FOCUSED
1492486 bias index: DIVERS

1494517 bias index: DIVERSIFIED
1494524 bias index: DIVERSIFIED
1494526 bias index: FOCUSED
1494545 bias index: DISPERSED
1494558 bias index: DIVERSIFIED
1494562 bias index: DIVERSIFIED
1494569 bias index: DIVERSIFIED
1494572 bias index: DIVERSIFIED
1494587 bias index: DIVERSIFIED
1494588 bias index: FOCUSED
1494592 bias index: DIVERSIFIED
1494598 bias index: DIVERSIFIED
1494604 bias index: DIVERSIFIED
1494608 bias index: DIVERSIFIED
1494610 bias index: DIVERSIFIED
1494612 bias index: DIVERSIFIED
1494613 bias index: DIVERSIFIED
1494615 bias index: DIVERSIFIED
1494621 bias index: DIVERSIFIED
1494632 bias index: DIVERSIFIED
1494645 bias index: DIVERSIFIED
1494658 bias index: FOCUSED
1494668 bias index: DIVERSIFIED
1494689 bias index: FOCUSED
1494692 bias index: DIVERSIFIED
1494694 bias index: DIVERSIFIED
1494716 bias index: DIVERSIFIED
1494732 bias index: DISPERSED
1494747 bias index: DIVERSIFIED
1494748 bias index: DIVERSIFIED
1494766 bias index: DIVERSIFIED
1494778 bias index: DIVERSIF

In [4]:
def iter_texts(infile):
        with open(infile) as f:
            for line in f:
                yield line
                
class jsonDocs(object):
    
    def __init__(self, infile):
        self.infile = infile
        
    def __iter__(self):
        for text in iter_texts(self.infile):
            yield json.loads(text)
        

In [7]:
texts = jsonDocs(infile="unparagraphed_validation_texts_analyzed_with_discoursebias.jsonl")

# results = [pool.apply(create_id_bias_list_of_tuples, args=(text,)) for text in texts] # bad, creates to many pools
ids = []
biases = []

for text in texts:
    ids.append(text["id"])
    biases.append(text["biasIndex"])

In [8]:
df = pd.DataFrame({"id":ids, "bias":biases})
print(df.head(3))
df.to_pickle("unparagraphed_article_validation_bypublisher_20181122.pickle")

        id         bias
0  0000017  Diversified
1  0000023  Diversified
2  0000029  Diversified
